## PROBLEM 4 (30 points)
### Who is the most popular actor in each country? The most popular actor of a country is the actor who was in the most films rented by customers from that country. There could be ties. For each country, display in a dataframe the country name, the highest actor film count of the country, and the name(s) of the most popular actor(s) of the country. If a country does not have a favorite actor, show "None" as the actor name. Only display results for countries whose names start with the letter 'A', and sort by country name.

In [ ]:
from data201 import db_connection, df_query
conn = db_connection(config_file='sakila.ini')

#### Countries whose names start with the letter 'A'.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        )
    SELECT * FROM countries ORDER BY country
    """
)

#### Customers' countries.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        )
    -- SELECT * FROM countries ORDER BY country
    SELECT * FROM customer_countries ORDER BY country
    """
)

#### Customers of countries whose names start with the letter 'A'.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    SELECT * FROM customers_by_country ORDER BY country
    """
)

#### Films rented by those customers.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        ),
        rented_films_by_country AS
        (
            SELECT country, film_id
            FROM customers_by_country
            LEFT OUTER JOIN rental USING (customer_id)
            LEFT OUTER JOIN inventory USING (inventory_id)
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    -- SELECT * FROM customers_by_country ORDER BY country
    SELECT * FROM rented_films_by_country ORDER BY country
    """
)

#### Actors in those rented films.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        ),
        rented_films_by_country AS
        (
            SELECT country, film_id
            FROM customers_by_country
            LEFT OUTER JOIN rental USING (customer_id)
            LEFT OUTER JOIN inventory USING (inventory_id)
        ),
        actors_in_rented_films_by_country AS
        (
            SELECT country, film_id, actor_id
            FROM rented_films_by_country
            LEFT OUTER JOIN film USING (film_id)
            LEFT OUTER JOIN film_actor USING (film_id)
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    -- SELECT * FROM customers_by_country ORDER BY country
    -- SELECT * FROM rented_films_by_country ORDER BY country
    SELECT * FROM actors_in_rented_films_by_country ORDER BY country
    """
)

#### Count of films by actors by country.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        ),
        rented_films_by_country AS
        (
            SELECT country, film_id
            FROM customers_by_country
            LEFT OUTER JOIN rental USING (customer_id)
            LEFT OUTER JOIN inventory USING (inventory_id)
        ),
        actors_in_rented_films_by_country AS
        (
            SELECT country, film_id, actor_id
            FROM rented_films_by_country
            LEFT OUTER JOIN film USING (film_id)
            LEFT OUTER JOIN film_actor USING (film_id)
        ),
        count_of_films_by_actor_by_country AS
        (
			SELECT country, actor_id,
                   COUNT(film_id) AS film_count
			FROM actors_in_rented_films_by_country
            GROUP BY country, actor_id
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    -- SELECT * FROM customers_by_country ORDER BY country
    -- SELECT * FROM rented_films_by_country ORDER BY country
    -- SELECT * FROM actors_in_rented_films_by_country ORDER BY country
    SELECT * FROM count_of_films_by_actor_by_country ORDER BY country, film_count DESC
    """
)

#### Maximum film count by actors by country.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        ),
        rented_films_by_country AS
        (
            SELECT country, film_id
            FROM customers_by_country
            LEFT OUTER JOIN rental USING (customer_id)
            LEFT OUTER JOIN inventory USING (inventory_id)
        ),
        actors_in_rented_films_by_country AS
        (
            SELECT country, film_id, actor_id
            FROM rented_films_by_country
            LEFT OUTER JOIN film USING (film_id)
            LEFT OUTER JOIN film_actor USING (film_id)
        ),
        count_of_films_by_actor_by_country AS
        (
			SELECT country, actor_id,
                   COUNT(film_id) AS film_count
			FROM actors_in_rented_films_by_country
            GROUP BY country, actor_id
        ),
        max_count_of_films_by_actor_by_country AS
        (
            SELECT country, 
                   MAX(film_count) AS max_film_count
            FROM count_of_films_by_actor_by_country
            GROUP BY COUNTRY
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    -- SELECT * FROM customers_by_country ORDER BY country
    -- SELECT * FROM rented_films_by_country ORDER BY country
    -- SELECT * FROM actors_in_rented_films_by_country ORDER BY country
    -- SELECT * FROM count_of_films_by_actor_by_country ORDER BY country, film_count DESC
    SELECT * FROM max_count_of_films_by_actor_by_country ORDER BY country
    """
)

#### Actors of each country whose film counts match the maximum film count.

In [ ]:
df_query(conn, 
    """
    WITH 
        countries AS
        (
            SELECT country_id, country 
            FROM country
            WHERE country LIKE 'A%'
        ),
        customer_countries AS
        (
			SELECT country, customer_id
            FROM customer
            JOIN address USING (address_id)
            JOIN city USING (city_id)
            JOIN countries USING (country_id)
        ),
        customers_by_country AS
        (
            SELECT country, customer_id
            FROM countries
            LEFT OUTER JOIN customer_countries USING (country)
        ),
        rented_films_by_country AS
        (
            SELECT country, film_id
            FROM customers_by_country
            LEFT OUTER JOIN rental USING (customer_id)
            LEFT OUTER JOIN inventory USING (inventory_id)
        ),
        actors_in_rented_films_by_country AS
        (
            SELECT country, film_id, actor_id
            FROM rented_films_by_country
            LEFT OUTER JOIN film USING (film_id)
            LEFT OUTER JOIN film_actor USING (film_id)
        ),
        count_of_films_by_actor_by_country AS
        (
			SELECT country, actor_id,
                   COUNT(film_id) AS film_count
			FROM actors_in_rented_films_by_country
            GROUP BY country, actor_id
        ),
        max_count_of_films_by_actor_by_country AS
        (
            SELECT country, 
                   MAX(film_count) AS max_film_count
            FROM count_of_films_by_actor_by_country
            GROUP BY COUNTRY
        ),
        actor_names AS
        (
            SELECT actor_id,
                   CONCAT(actor.first_name, ' ', actor.last_name) 
                       AS actor_name
            FROM actor
            ORDER BY actor_id
        ),
        most_popular_actors_by_country AS
        (
            SELECT country, max_film_count, 
                   actor_name AS most_popular_actors
            FROM count_of_films_by_actor_by_country
            JOIN max_count_of_films_by_actor_by_country USING (country)
            LEFT OUTER JOIN actor_names USING (actor_id)
            WHERE film_count = max_film_count
        )
    -- SELECT * FROM countries ORDER BY country
    -- SELECT * FROM customer_countries ORDER BY country
    -- SELECT * FROM customers_by_country ORDER BY country
    -- SELECT * FROM rented_films_by_country ORDER BY country
    -- SELECT * FROM actors_in_rented_films_by_country ORDER BY country
    -- SELECT * FROM count_of_films_by_actor_by_country ORDER BY country, film_count DESC
    -- SELECT * FROM max_count_of_films_by_actor_by_country ORDER BY country
    SELECT * FROM most_popular_actors_by_country ORDER BY country
    """
)

In [ ]:
conn.close()